In [1]:
import numpy as np
from numpy.linalg import det
import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib.ticker import LinearLocator
from genetic_one import Gen1

In [ ]:
class Central_Generation(gen1):
    
        def first_generation(self):
        """
        This function will generate a random generation of possible solutions based on the model hyper parameters
        :return::[[int, int ,...],[int,..]]
        """
        generation_0 = []

        number_of_cells = self._nr_cells()

        for cell_nr in range(number_of_cells):
            cell_constrains = []

            for f in range(self.input_size):
                feature = self.input_size - f - 1
                cell_coordinate = int(cell_nr / (self.model_par["cell_split_number"] ** feature))
                cell_nr = cell_nr - cell_coordinate * int((self.model_par["cell_split_number"] ** feature))

                interval = (-self.input_ranges[feature][0] + self.input_ranges[feature][1]) / self.model_par[
                    'cell_split_number']
                c_0 = self.input_ranges[feature][0] + interval * cell_coordinate
                c_1 = self.input_ranges[feature][0] + interval * (cell_coordinate + 1)
                constrain = [c_0, c_1]
                cell_constrains.append(constrain)

            for subject_number in range(self.model_par["subjects_in_cell"]):
                subject = []
                for feature_bound in cell_constrains:
                    # print(feature_bound)
                    subject.append(random.randint(int(feature_bound[0]), int(feature_bound[1])))
                generation_0.append(subject)

        return generation_0

In [2]:
a1 = [1,0]; a2=[0,1];
A  = np.transpose([a1,a2]);

theta =  np.pi/4;
R = [ [ np.cos(theta), -np.sin(theta)], [ np.sin(theta),  np.cos(theta)] ];

b1 = np.sqrt(2)*np.dot(R,a1);  b2 = a2 #np.sqrt(2)*np.dot(R,a2);
B  = np.transpose([b1,b2]);

a = A#np.array([[0,1],[1,0]])
b = B#np.array([[0,5],[5,0]])

In [3]:

eps = 0.0001

bond=10

def tAtB(params):
    tA = np.array([[params[0],params[1]],
                   [params[2],params[3]]])
    tB = np.array([[params[4],params[5]],
                   [params[6],params[7]]])
    return tA, tB
          

def fit_fucntion(params , k_p=1):
          
        tA, tB= tAtB(params)
        tAa= np.dot(tA,a)
        tBa= np.dot(tB,b)
        
        zero_mat= tAa - tBa
        
        s=0
        for row in zero_mat:
            for e in row:
                s+=e*e
        
        A_max=(bond+bond)**2* np.max([np.linalg.det(a),np.linalg.det(b)])
        A_min =np.min([np.linalg.det(a),np.linalg.det(b)])
        
        detTAa= det(tAa)*det(tAa) # minimum but biger than 0
        detTBa= det(tBa)*det(tBa)
        
        A_incentive = A_max/detTAa  + detTAa/A_min #(1-inf)
        B_incentive = A_max/detTBa  + detTBa/A_min
        f = (s/A_min)**k_p + A_incentive + B_incentive 
        
        print("s:",s)
        print("A_incentive",A_incentive)
        print("B_incentive",B_incentive)
        
        return f 

In [4]:
# Experiment settings

#Hyperparameters of the model
model_par = {
    
    'cell_split_number': 2, 
    'subjects_in_cell': 5,

    'nr_clones': 10,
    'mutation_gaussian_sd': 2,

    'pins': 8,
    'gene_quality': 1,
    
}




input_size = 8 # P=[tA00,tA01,tA10,tA11,tB00,tB01,tB10,tB11]

bounds =[[-bond,bond]for _ in range(input_size)] # searching intervals for the solution

# Experiment
experiment = Gen1(fit_fucntion ,input_size, bounds, model_par)

In [5]:
## Automate evolution

nr_epochs = 90
last_generation = experiment.evolve(nr_epochs)
fit = [fit_fucntion(x) for x in last_generation] 
print("fit:",fit)


Epochs 0/90
s: 197.0000000000001
A_incentive 146.77777777777777
B_incentive 47.111111111111185
s: 197.0000000000001
A_incentive 146.77777777777777
B_incentive 47.111111111111185
s: 249.0000000000001
A_incentive 841.4756242568366
B_incentive 441.9070294784585
s: 228.0000000000001
A_incentive 400.9999999999998
B_incentive 325.2345679012347
s: 72.00000000000004
A_incentive 57.16326530612246
B_incentive 1681.237953599049
s: 188.00000000000009
A_incentive inf
B_incentive 226.777777777778
s: 268.0000000000001
A_incentive 400.9999999999999
B_incentive 53.44444444444467
s: 49.00000000000002
A_incentive 676.5917159763308
B_incentive 400.9999999999996
s: 243.0000000000001
A_incentive 41.000000000000014
B_incentive 198.04081632653086
s: 185.0000000000001
A_incentive 226.77777777777757
B_incentive 1764.2267573696163
s: 90.00000000000004
A_incentive 41.000000000000014
B_incentive 625.6400000000003
s: 135.00000000000009
A_incentive 103.99999999999997
B_incentive 1296.3086419753106
s: 30.000000000000

C:\Users\tomut\AppData\Local\Temp\ipykernel_12140\3388858537.py:32: RuntimeWarning: divide by zero encountered in double_scalars
  A_incentive = A_max/detTAa  + detTAa/A_min #(1-inf)
C:\Users\tomut\AppData\Local\Temp\ipykernel_12140\3388858537.py:33: RuntimeWarning: divide by zero encountered in double_scalars
  B_incentive = A_max/detTBa  + detTBa/A_min


s: 325.00000000000006
A_incentive 576.6944444444441
B_incentive 1764.2267573696163
s: 282.0
A_incentive 3364.1189060642073
B_incentive 4356.091827364558
s: 318.00000000000006
A_incentive 729.5486968449932
B_incentive 3600.1111111111154
s: 324.0000000000001
A_incentive 1444.2770083102505
B_incentive 2916.137174211249
s: 420.00000000000006
A_incentive 3600.1111111111095
B_incentive 8649.046248121176
s: 503.0000000000001
A_incentive 2809.142399430403
B_incentive 13689.029220542048
s: 270.00000000000006
A_incentive 3600.1111111111154
B_incentive 9216.043402777792
s: 355.0
A_incentive 4900.081632653065
B_incentive 1296.3086419753097
s: 355.0
A_incentive 4900.081632653065
B_incentive 1296.3086419753097
s: 162.00000000000006
A_incentive 576.6944444444441
B_incentive 103.99999999999982
s: 394.0
A_incentive 2500.160000000001
B_incentive 1521.2629848783706
s: 292.0
A_incentive 3600.1111111111154
B_incentive 1936.2066115702494
s: 180.0
A_incentive 8649.046248121176
B_incentive 171.36686390532557


s: 54.99999999999999
A_incentive 41.000000000000014
B_incentive 226.777777777778
s: 83.0
A_incentive 41.0
B_incentive 2704.1479289940867
s: 97.0
A_incentive 47.111111111111114
B_incentive 484.8264462809919
s: 102.0
A_incentive 85.93827160493825
B_incentive 3600.1111111111154
s: 99.0
A_incentive inf
B_incentive 729.548696844994
s: 147.00000000000003
A_incentive 104.00000000000006
B_incentive 2916.1371742112515
s: 287.0
A_incentive 9216.043402777776
B_incentive 1089.3673094582196
s: 287.0
A_incentive 9216.043402777776
B_incentive 1089.3673094582196
s: 257.00000000000006
A_incentive 2401.1665972511446
B_incentive 1089.3673094582196
s: 518.0000000000002
A_incentive 6724.059488399765
B_incentive 2601.153787005
s: 463.00000000000006
A_incentive 9216.043402777776
B_incentive 484.8264462809919
s: 334.0
A_incentive 10404.03844675126
B_incentive 2500.160000000001
s: 245.00000000000006
A_incentive 4489.089106705276
B_incentive 784.5102040816332
s: 108.0
A_incentive 5776.069252077562
B_incentive 4

s: 845.0000000000003
A_incentive 198.04081632653052
B_incentive 2704.1479289940867
s: 701.0000000000002
A_incentive 3600.1111111111154
B_incentive 8100.049382716049
s: 701.0000000000002
A_incentive 3600.1111111111154
B_incentive 8100.049382716049
s: 647.0000000000002
A_incentive 900.4444444444454
B_incentive 8649.046248121176
s: 678.0000000000002
A_incentive 2809.142399430401
B_incentive 9025.04432132964
s: 405.00000000000006
A_incentive 3136.127551020405
B_incentive 576.6944444444451
s: 557.0
A_incentive 2116.189035916824
B_incentive 2025.1975308641968
s: 587.0000000000002
A_incentive 576.6944444444441
B_incentive 6400.062499999995
s: 451.0
A_incentive 1156.346020761246
B_incentive 7225.055363321802
s: 494.0
A_incentive 2116.189035916824
B_incentive 3136.1275510204105
s: 434.0000000000001
A_incentive 1225.3265306122444
B_incentive 2209.1810774105925
s: 485.00000000000006
A_incentive 3364.1189060642073
B_incentive 5041.0793493354495
s: 450.0000000000001
A_incentive 2916.137174211249
B_

...

s: 20.0
A_incentive 53.44444444444444
B_incentive 41.000000000000014
s: 20.0
A_incentive 53.44444444444444
B_incentive 41.000000000000014
s: 46.000000000000014
A_incentive 53.444444444444464
B_incentive 70.25000000000003
s: 54.0
A_incentive 41.00000000000001
B_incentive 47.11111111111114
s: 110.00000000000003
A_incentive 104.00000000000003
B_incentive 257.5625000000002
s: 93.0
A_incentive 41.00000000000001
B_incentive 70.25000000000003
s: 52.0
A_incentive 401.0000000000001
B_incentive 226.777777777778
s: 93.00000000000001
A_incentive 41.00000000000001
B_incentive 104.00000000000004
s: 43.0
A_incentive 47.111111111111114
B_incentive 47.11111111111114
s: 207.00000000000003
A_incentive 41.00000000000001
B_incentive 1089.3673094582196
s: 60.0
A_incentive 401.0000000000001
B_incentive 57.16326530612246
s: 56.000000000000014
A_incentive 104.00000000000003
B_incentive 257.5625000000002
s: 20.0
A_incentive 53.44444444444444
B_incentive 41.000000000000014
s: 20.0
A_incentive 53.44444444444444
B

s: 20.0
A_incentive 53.44444444444444
B_incentive 41.000000000000014
s: 20.0
A_incentive 53.44444444444444
B_incentive 41.000000000000014
s: 58.000000000000014
A_incentive 401.0000000000001
B_incentive 85.93827160493836
s: 54.00000000000003
A_incentive 53.444444444444464
B_incentive 146.7777777777779
s: 84.0
A_incentive 41.00000000000001
B_incentive 146.7777777777779
s: 86.0
A_incentive 104.00000000000006
B_incentive inf
s: 57.000000000000014
A_incentive 41.00000000000001
B_incentive 1849.216333153057
s: 65.0
A_incentive 124.30578512396698
B_incentive 146.77777777777777
s: 177.0
A_incentive inf
B_incentive 47.11111111111114
s: 29.0
A_incentive 41.00000000000001
B_incentive 325.2345679012347
s: 79.00000000000001
A_incentive 104.00000000000004
B_incentive 1764.2267573696151
s: 79.00000000000001
A_incentive 41.00000000000001
B_incentive 484.8264462809919
s: 20.0
A_incentive 53.44444444444444
B_incentive 41.000000000000014
s: 20.0
A_incentive 53.44444444444444
B_incentive 41.00000000000001

s: 18.0
A_incentive 41.0
B_incentive 41.0
s: 18.0
A_incentive 41.0
B_incentive 41.0
s: 62.000000000000014
A_incentive 70.24999999999997
B_incentive 290.3840830449827
s: 135.0
A_incentive 103.99999999999997
B_incentive 85.93827160493836
s: 91.0
A_incentive 41.00000000000001
B_incentive 104.00000000000004
s: 117.00000000000003
A_incentive 103.99999999999997
B_incentive 362.1080332409973
s: 9.0
A_incentive 70.24999999999997
B_incentive 400.9999999999992
s: 70.0
A_incentive 1521.262984878369
B_incentive 576.6944444444441
s: 96.00000000000001
A_incentive 85.93827160493825
B_incentive 2025.1975308641968
s: 56.0
A_incentive 226.77777777777777
B_incentive 57.16326530612248
s: 84.0
A_incentive 226.77777777777777
B_incentive 171.36686390532543
s: 70.00000000000003
A_incentive 226.77777777777777
B_incentive 198.04081632653072
s: 11.0
A_incentive 41.00000000000001
B_incentive inf
s: 11.0
A_incentive 41.00000000000001
B_incentive inf
s: 231.00000000000009
A_incentive inf
B_incentive 104.00000000000

s: 20.0
A_incentive 53.44444444444444
B_incentive 41.000000000000014
s: 20.0
A_incentive 53.44444444444444
B_incentive 41.000000000000014
s: 143.0
A_incentive 400.9999999999998
B_incentive 484.8264462809919
s: 11.999999999999998
A_incentive 146.77777777777777
B_incentive 146.77777777777777
s: 43.0
A_incentive 362.10803324099714
B_incentive 104.00000000000003
s: 66.0
A_incentive 401.0000000000001
B_incentive 257.5625000000002
s: 20.0
A_incentive 103.99999999999997
B_incentive 400.99999999999994
s: 21.000000000000004
A_incentive 70.24999999999997
B_incentive 257.5625000000002
s: 96.0
A_incentive 41.00000000000001
B_incentive 784.5102040816332
s: 73.0
A_incentive 198.04081632653072
B_incentive 529.7561436672968
s: 18.000000000000004
A_incentive 41.0
B_incentive 70.25000000000003
s: 65.00000000000003
A_incentive 85.9382716049383
B_incentive 257.5625000000002
s: 20.0
A_incentive 53.44444444444444
B_incentive 41.000000000000014
s: 20.0
A_incentive 53.44444444444444
B_incentive 41.00000000000

s: 18.0
A_incentive 41.0
B_incentive 41.0
s: 18.0
A_incentive 41.0
B_incentive 41.0
s: 20.999999999999993
A_incentive 146.77777777777777
B_incentive 41.000000000000014
s: 28.000000000000014
A_incentive 401.0000000000003
B_incentive 676.5917159763321
s: 51.000000000000014
A_incentive 103.99999999999999
B_incentive 85.9382716049383
s: 85.0
A_incentive 104.00000000000003
B_incentive 401.0000000000003
s: 6.0
A_incentive 70.24999999999997
B_incentive 70.24999999999997
s: 42.0
A_incentive inf
B_incentive 47.11111111111113
s: 70.0
A_incentive inf
B_incentive 362.10803324099714
s: 33.0
A_incentive inf
B_incentive 226.77777777777777
s: 58.0
A_incentive 257.56249999999994
B_incentive inf
s: 87.00000000000001
A_incentive inf
B_incentive 171.36686390532557
s: 21.0
A_incentive 47.111111111111114
B_incentive 41.0
s: 21.0
A_incentive 47.111111111111114
B_incentive 41.0
s: 8.999999999999996
A_incentive 41.0
B_incentive 47.11111111111114
s: 50.0
A_incentive 146.77777777777777
B_incentive 146.7777777777

In [6]:
best =last_generation [fit.index(min(fit))]
print(best)

[-3, -1, -4, -3, 2, -3, 0, -3]


In [7]:
P= best#[2, 1, -8, -3, 1, 0, 0, -1]
tA,tB = tAtB(P)
zero_mat= np.dot(tA,a) - np.dot(tB,b)
print("\n _____\n tA:\n",tA)
print("\n _____\n tB:\n",tB)

print("\n zero_mat:\n",zero_mat)


 _____
 tA:
 [[-3 -1]
 [-4 -3]]

 _____
 tB:
 [[ 2 -3]
 [ 0 -3]]

 zero_mat:
 [[-2.  2.]
 [-1.  0.]]
